#### Jupyter Notebook for Dashboard 



In [1]:
# imports
import os
import requests
import json
import pandas as pd
from dotenv import load_dotenv
from requests import Request, Session
from requests.exceptions import ConnectionError, Timeout, TooManyRedirects
import json
import panel as pn
pn.extension('plotly')
import plotly.express as px
import hvplot.pandas
import matplotlib.pyplot as plt
import pandas as pd
from pathlib import Path
import seaborn as sns

%matplotlib inline
from panel.layout.gridstack import GridStack
from panel.interact import interact, interactive, fixed, interact_manual

In [2]:
# Initialize the Panel Extensions (for Plotly)
import panel as pn
pn.extension("plotly")

In [3]:
#Use one new Python library that hasn't been covered in class. (Yfinance is yahoo finance)
import yfinance as yf

In [4]:
# Load .env enviroment variables
load_dotenv()

True

### Import Covid-19 Case Data

In [5]:
#data collected from the World Health Organization
#https://covid19.who.int/info/
    
csv_path = Path("../Resources/WHO-COVID-19-global-data.csv")
df_covid_cases = pd.read_csv(csv_path)
df_covid_cases.head()


Date_reported Country_code      Country WHO_region  New_cases  \
0    2020-01-03           AF  Afghanistan       EMRO          0   
1    2020-01-04           AF  Afghanistan       EMRO          0   
2    2020-01-05           AF  Afghanistan       EMRO          0   
3    2020-01-06           AF  Afghanistan       EMRO          0   
4    2020-01-07           AF  Afghanistan       EMRO          0   

   Cumulative_cases  New_deaths  Cumulative_deaths  
0                 0           0                  0  
1                 0           0                  0  
2                 0           0                  0  
3                 0           0                  0  
4                 0           0                  0

### Ben's Globally available data

In [6]:
# BEN GLOBAL DATA SECTION 
btc= yf.Ticker("BTC-USD")

#get BTC pre and post covid data 
btc_historical_precovid = btc.history(start="2018-03-01", end="2020-03-01")
btc_historical_postcovid = btc.history(start="2020-03-01", end="2021-06-01")
btc_historical_precovid.drop(btc_historical_precovid.columns.difference(['Close']), 1, inplace=True)
btc_historical_postcovid.drop(btc_historical_postcovid.columns.difference(['Close']), 1, inplace=True)

#Change close to specific column name 
btc_historical_precovid = btc_historical_precovid.rename(columns={"Close": "BTC"})
#Change close to specific column name btc_historical_postcovid
btc_historical_postcovid = btc_historical_postcovid.rename(columns={"Close": "BTC"})

#Ethereum get pre and post data 
eth= yf.Ticker("ETH-USD")
eth_historical_precovid = eth.history(start="2018-03-01", end="2020-03-01")
eth_historical_postcovid = eth.history(start="2020-03-01", end="2021-03-01")
eth_historical_precovid.drop(eth_historical_precovid.columns.difference(['Close']), 1, inplace=True)
eth_historical_postcovid.drop(eth_historical_postcovid.columns.difference(['Close']), 1, inplace=True)
 #Change close to specific column name 
eth_historical_precovid = eth_historical_precovid.rename(columns={"Close": "ETH"})
#Change close to specific column name 
eth_historical_postcovid = eth_historical_postcovid.rename(columns={"Close": "ETH"})

#litecoin get pre and post data 
ltc= yf.Ticker("LTC-USD")
ltc_historical_precovid = ltc.history(start="2018-03-01", end="2020-03-01")
ltc_historical_postcovid = ltc.history(start="2020-03-01", end="2021-03-01")
ltc_historical_precovid.drop(ltc_historical_precovid.columns.difference(['Close']), 1, inplace=True)
ltc_historical_postcovid.drop(ltc_historical_postcovid.columns.difference(['Close']), 1, inplace=True)
ltc_historical_precovid = ltc_historical_precovid.rename(columns={"Close": "LTC"})
ltc_historical_postcovid = ltc_historical_postcovid.rename(columns={"Close": "LTC"})

#VanEck Vectors Semiconductor ETF (SMH)  get pre and post data 

smh= yf.Ticker("SMH")
semiconductor_historical_precovid = smh.history(start="2018-03-01", end="2020-03-01")
semiconductor_historical_postcovid = smh.history(start="2020-03-01", end="2021-03-01")
semiconductor_historical_precovid.drop(semiconductor_historical_precovid.columns.difference(['Close']), 1, inplace=True)
semiconductor_historical_postcovid.drop(semiconductor_historical_postcovid.columns.difference(['Close']), 1, inplace=True)
semiconductor_historical_precovid = semiconductor_historical_precovid.rename(columns={"Close": "Semiconductor ETF"})
semiconductor_historical_postcovid = semiconductor_historical_postcovid.rename(columns={"Close": "Semiconductor ETF"})
 
# PRE-COVID Join ETH, BTC, LTC and Semiconductor data daily Returns into a single DataFrame with columns for each portfolio's returns.

pre_covid_combined_df = pd.concat([btc_historical_precovid, eth_historical_precovid, ltc_historical_precovid,semiconductor_historical_precovid], axis="columns", join="inner")
# Sort datetime index in ascending order (past to present)
pre_covid_combined_df.sort_index(inplace=True)

# POST-COVID Join ETH, BTC, LTC and Semiconductor data daily Returns into a single DataFrame with columns for each portfolio's returns.

post_covid_combined_df = pd.concat([btc_historical_postcovid, eth_historical_postcovid, ltc_historical_postcovid,semiconductor_historical_postcovid], axis="columns", join="inner")

# Sort datetime index in ascending order (past to present)
post_covid_combined_df.sort_index(inplace=True)

# Plot daily returns of all portfolios
#PRE-COVID
pre_daily_returns = pre_covid_combined_df.pct_change()
#print(pre_daily_returns.head())

# Plot daily returns of all portfolios
#POST-COVID
post_daily_returns = post_covid_combined_df.pct_change()

# Calculate cumulative returns of all portfolios
pre_cumulative_returns = (1 + pre_daily_returns).cumprod() - 1
# Calculate cumulative returns of all portfolios
post_cumulative_returns = (1 + post_daily_returns).cumprod() - 1

#COVID data from World Health Organization 

#cleaning and sorting data 
df_covid_cases = df_covid_cases.dropna().copy()
df_covid_cases = df_covid_cases.drop(columns=['Country_code'])
df_covid_cases = df_covid_cases.rename(columns={"Date_reported": "Date"})
df_covid_cases = df_covid_cases.sort_values(by=["Date"], ascending=True)

#change data structure 
df_covid_cases = df_covid_cases.set_index('Date')
sorted = df_covid_cases.sort_values(by=['New_cases'], ascending=False)
peak_covid_case_date = df_covid_cases.nlargest(1, 'New_cases')
df_covid_cases = df_covid_cases.drop(columns=['WHO_region','New_cases','New_deaths','Cumulative_deaths'])

#set dates to match cryptocurrency and semiconductor dates 
df_covid_cases = df_covid_cases[(df_covid_cases.index > '2020-03-01') & (df_covid_cases.index <= '2021-06-01')]

#pseudo-code: all covid cases grouped by date
#sum up the cases 
df_covid_cumulative_cases = df_covid_cases.groupby([df_covid_cases.index]).sum()
df_covid_cumulative_cases.reset_index( inplace=True)
idx = pd.Index(df_covid_cumulative_cases.index)
print("Any Duplicates found: ", pd.Series(idx.duplicated()).any())

#plot cases
post_covid_combined_df.reset_index( inplace=True)
df_covid_cumulative_cases.reset_index( inplace=True)
ben_df_cumu_cases = df_covid_cumulative_cases
#combined dataframe
frames = [post_covid_combined_df,df_covid_cumulative_cases]
result = pd.concat(frames, axis=1,join="outer")

 
print(ben_df_cumu_cases.head())

C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:7: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  import sys
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:8: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:19: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:20: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:30: FutureWarning: In a future version of pandas all arguments of 

Any Duplicates found:  False
   index        Date  Cumulative_cases
0      0  2020-03-02             88914
1      1  2020-03-03             91233
2      2  2020-03-04             94192
3      3  2020-03-05             96599
4      4  2020-03-06            100206


C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:40: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:41: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only


### Ben's Data for Crypto Vs. Semiconductor Analysis 

In [7]:
#setting comensurate fictious values for crypto and semiconductor ETF
#values are set to be balanced with 1 BTC
#underlying assumption: the investor is heavily invested in semiconductors 

btc_holding_amount = 1
eth_holding_amount = 10.00
ltc_holding_amount = 10.00
semiconductor_ETF_holding_amount = 200.00

#scenario 1: 2020-03-01 (START OF COVID ERA)

#btc closing value for 2020-03-01 
btc_close_price_1 =  btc.history(start="2020-03-01", end="2020-03-01")
btc_close_price_date1 = btc_close_price_1.iloc[0]['Close']


#eth closing value for 2020-03-01 
eth_close_price_1 =  eth.history(start="2020-03-01", end="2020-03-01")
eth_close_price_date1 = eth_close_price_1.iloc[0]['Close']


#litecoin closing value for 2020-03-01 
ltc_close_price_1 =  ltc.history(start="2020-03-01", end="2020-03-01")
ltc_close_price_date1 = ltc_close_price_1.iloc[0]['Close']

#semiconductor closing value for 2020-03-01 
semic_close_price_1 =  smh.history(start="2020-03-01")
semic_close_price_date1 = semic_close_price_1.iloc[0]['Close']

#Scenario 1:  Compute and print 2020-03-01 value of my assets: 
btc_value_1 = (btc_holding_amount) * (btc_close_price_date1)
eth_value_1 = (eth_holding_amount) * (eth_close_price_date1)
ltc_value_1 = (ltc_holding_amount) * (ltc_close_price_date1)
semiconductor_value_1 = (semiconductor_ETF_holding_amount) * (semic_close_price_date1)

#scenario 2: 2021-05-07: (PEAK OF COVID CASES)
#btc closing value for 2021-05-07
btc_close_price_2 =  btc.history(start="2021-05-07", end="2021-05-07")
btc_close_price_date2 = btc_close_price_2.iloc[0]['Close']
#eth closing value for 2021-05-07
eth_close_price_2 =  eth.history(start="2021-05-07", end="2021-05-07")
eth_close_price_date2 = eth_close_price_2.iloc[0]['Close']

#litecoin closing value for 2021-05-07
ltc_close_price_2 =  ltc.history(start="2021-05-07", end="2021-05-07")
ltc_close_price_date2 = ltc_close_price_2.iloc[0]['Close']

#semiconductor closing value for 2021-05-07
semic_close_price_2 =  smh.history(start="2021-05-07")
semic_close_price_date2 = semic_close_price_2.iloc[0]['Close']

#Scenario 2:  Compute and print 2021-05-07 value of my assets: 
btc_value_2 = (btc_holding_amount) * (btc_close_price_date2)
eth_value_2 = (eth_holding_amount) * (eth_close_price_date2)
ltc_value_2 = (ltc_holding_amount) * (ltc_close_price_date2)
semiconductor_value_2 = (semiconductor_ETF_holding_amount) * (semic_close_price_date2)

#scenario 3: 2021-06-01 (RECENT DATE DATA):

#btc closing value for 2021-06-01
btc_close_price_3 =  btc.history(start="2021-06-01", end="2021-06-01")
btc_close_price_date3 = btc_close_price_3.iloc[0]['Close']

#eth closing value for 2021-06-01
eth_close_price_3 =  eth.history(start="2021-06-01", end="2021-06-01")
eth_close_price_date3 = eth_close_price_3.iloc[0]['Close']

#litecoin closing value for 2021-06-01
ltc_close_price_3 =  ltc.history(start="2021-06-01", end="2021-06-01")
ltc_close_price_date3 = ltc_close_price_3.iloc[0]['Close']

#semiconductor closing value for 2021-06-01
semic_close_price_3 =  smh.history(start="2021-06-01")
semic_close_price_date3 = semic_close_price_3.iloc[0]['Close']

#Scenario 3:  Compute and print 2021-06-01 value of my assets: 
btc_value_3 = (btc_holding_amount) * (btc_close_price_date3)
eth_value_3 = (eth_holding_amount) * (eth_close_price_date3)
ltc_value_3 = (ltc_holding_amount) * (ltc_close_price_date3)
semiconductor_value_3 = (semiconductor_ETF_holding_amount) * (semic_close_price_date3)

#display data 
d = {'date': ["2020-03-01", "2021-05-07","2021-06-01"], 'BTC': [btc_value_1,btc_value_2,btc_value_3], 'ETH': [eth_value_1,eth_value_2,eth_value_3], 'LTC': [ltc_value_1,ltc_value_2,ltc_value_3],'Semiconductor ETF': [semiconductor_value_1,semiconductor_value_2,semiconductor_value_3]}
df_value_comparison = pd.DataFrame(data=d)
compare_results= df_value_comparison.set_index('date')
 

In [8]:
# BEN METHODS SECTION 
#pre_daily_returns.hvplot(height=600, width =900,title='Pre-Covid Daily Returns, Combined')

### Sadia's Globally available data

In [9]:
# SADIA GLOBAL DATA SECTION 
# Set tickers for the cryptocurrency we are using in our analysis, that is, Bitcoin, Ethereum, and Lite Coin
BTC = yf.Ticker("BTC-USD")
ETH = yf.Ticker("ETH-USD")
LTC = yf.Ticker("LTC-USD")
Gold = yf.Ticker("GC=F")

# Pull the data for all our variables. We'll pull the combined data from Pre-Covid era (1 Mar 2018) to most recently (1 June 2021) and slice it for our pre-covid and post covid analysis 
btc_data = BTC.history(start="2018-03-01", end="2021-06-01", actions=False)
eth_data = ETH.history(start="2018-03-01", end="2021-06-01")
ltc_data = LTC.history(start="2018-03-01", end="2021-06-01")
gold_data = Gold.history(start="2018-03-01", end="2021-06-01")

# Dropping unrequired columns
btc_data = btc_data.drop(columns=['Open', 'High', 'Low', 'Volume']).rename(columns={"Close": "BTC"})
eth_data = eth_data.drop(columns=['Open', 'High', 'Low', 'Volume', 'Dividends', 'Stock Splits']).rename(columns={"Close": "ETH"})
ltc_data = ltc_data.drop(columns=['Open', 'High', 'Low', 'Volume', 'Dividends', 'Stock Splits']).rename(columns={"Close": "LTC"})
gold_data = gold_data.drop(columns=['Open', 'High', 'Low', 'Volume', 'Dividends', 'Stock Splits']).rename(columns={"Close": "Gold"})

# Join the data into one dataframe
combined_df = pd.concat([btc_data, eth_data, ltc_data, gold_data], axis="columns", join="inner")

### PRECOVID ANALYSIS

# Slice/segregate the data for the precovid era
precovid_data = combined_df['20180301':'20200301']

# Calculation for daily returns:
daily_returns = precovid_data.pct_change().dropna().copy()

# Calculation for cumulative returns
cumulative_returns = (1 + daily_returns).cumprod() - 1

# Calculate and plotting the correlation
correlation = daily_returns.corr()

### POST COVID ANALYSIS

# Slice/segregate the data for the precovid era
postcovid_data = combined_df['20200301':'20210601']

# Calculation for daily returns:
daily_returns_post_covid = postcovid_data.pct_change().dropna().copy()

# Calculation for cumulative returns
cumulative_returns_post_covid = (1 + daily_returns_post_covid).cumprod() - 1

# Calculate and plotting the correlation and compare it with the correlation pre-covid
correlation_post_covid = daily_returns_post_covid.corr()

# We will calculate and plot the cumulative returns for the entire dataframe pre and post covid era to see the variation in cumulative returns over the entire period 
daily_returns_overall = combined_df.pct_change().dropna().copy()
cumulative_returns_overall = (1 + daily_returns_overall).cumprod() - 1

### WHO COVID CASES DATA

# Read in data from resource - covid cases from WHO
csv_path = Path("../Resources/WHO-COVID-19-global-data.csv")
df_covid_cases = pd.read_csv(csv_path)
df_covid_cases.isnull().sum()
df_covid_cases = df_covid_cases.dropna().copy()
df_covid_cases_clean = df_covid_cases.drop(columns=['Country_code', 'Country', 'WHO_region', 'New_cases', 'New_deaths', 'Cumulative_deaths']).set_index('Date_reported')
df_covid_cases_clean = df_covid_cases_clean[(df_covid_cases_clean.index > '2020-02-29') & (df_covid_cases_clean.index <= '2021-06-01')]
df_covid_cases_clean.index.names = ['Date']
df_covid_cumulative_cases = df_covid_cases_clean.groupby([df_covid_cases_clean.index]).sum()

In [10]:
#SADIA METHODS SECTION 
# Set asset volume:
btc_asset = 0.5
eth_asset = 5
ltc_asset = 35
gold_asset = 5

# Situation 1
# Print closing prices on 2020-03-01:
btc_close_price_1 = combined_df.loc["20200302"]["BTC"]
eth_close_price_1 = combined_df.loc["20200302"]["ETH"]
ltc_close_price_1 = combined_df.loc["20200302"]["LTC"]
gold_close_price_1 = combined_df.loc["20200302"]["Gold"]

# Compute current value of my assets
btc_value_1 = (btc_asset) * (btc_close_price_1)
eth_value_1 = (eth_asset) * (eth_close_price_1)
ltc_value_1 = (ltc_asset) * (ltc_close_price_1)
gold_value_1 = (gold_asset) * (gold_close_price_1)

# Situation 2
# Print closing prices on 2021-05-07:
btc_close_price_2 = combined_df.loc["20210507"]["BTC"]
eth_close_price_2 = combined_df.loc["20210507"]["ETH"]
ltc_close_price_2 = combined_df.loc["20210507"]["LTC"]
gold_close_price_2 = combined_df.loc["20210507"]["Gold"]

# Compute current value of my assets
btc_value_2 = (btc_asset) * (btc_close_price_2)
eth_value_2 = (eth_asset) * (eth_close_price_2)
ltc_value_2 = (ltc_asset) * (ltc_close_price_2)
gold_value_2 = (gold_asset) * (gold_close_price_2)

# Situation 3 
# Print closing prices on 2021-06-01:
btc_close_price_3 = combined_df.loc["20210601"]["BTC"]
eth_close_price_3 = combined_df.loc["20210601"]["ETH"]
ltc_close_price_3 = combined_df.loc["20210601"]["LTC"]
gold_close_price_3 = combined_df.loc["20210601"]["Gold"]

# Compute current value of my assets
btc_value_3 = (btc_asset) * (btc_close_price_3)
eth_value_3 = (eth_asset) * (eth_close_price_3)
ltc_value_3 = (ltc_asset) * (ltc_close_price_3)
gold_value_3 = (gold_asset) * (gold_close_price_3)

# Concat the investment data into one:
df = {'Date': ["2020-03-01", "2021-05-07","2021-06-01"], 
      'BTC': [btc_value_1,btc_value_2,btc_value_3], 
      'ETH': [eth_value_1,eth_value_2,eth_value_3], 
      'LTC': [ltc_value_1,ltc_value_2,ltc_value_3],
      'Gold': [gold_value_1,gold_value_2,gold_value_3]}
investment_df = pd.DataFrame(data=df)

### Mo's Globally available data

In [11]:
# MO GLOBAL DATA SECTION 
# MO GLOBAL DATA SECTION 
#Setting the tickers for the stocks picked

tesla = yf.Ticker("TSLA")
gamestop = yf.Ticker("GME")
amc = yf.Ticker("AMC")
blackberry = yf.Ticker("BB")
btc= yf.Ticker("BTC-USD")

# Pulling data for all stocks to be used precovid
tesla_historical_precovid = tesla.history(start="2018-03-01", end="2020-03-01")
gamestop_historical_precovid = gamestop.history(start="2018-03-01", end="2020-03-01")
amc_historical_precovid = amc.history(start="2018-03-01", end="2020-03-01")
blackberry_historical_precovid = blackberry.history(start="2018-03-01", end="2020-03-01")
btc_historical_precovid = btc.history(start="2018-03-01", end="2020-03-01")

# Cleaning data for all stocks to be used precovid
tesla_historical_precovid.drop(tesla_historical_precovid.columns.difference(['Close']), 1, inplace=True)
gamestop_historical_precovid.drop(gamestop_historical_precovid.columns.difference(['Close']), 1, inplace=True) 
amc_historical_precovid.drop(amc_historical_precovid.columns.difference(['Close']), 1, inplace=True) 
blackberry_historical_precovid.drop(blackberry_historical_precovid.columns.difference(['Close']), 1, inplace=True) 
btc_historical_precovid.drop(btc_historical_precovid.columns.difference(['Close']), 1, inplace=True) 

# Cleaning final dataframe for precovid

tesla_historical_precovid = tesla_historical_precovid.rename(columns={'Close': 'Tesla'})
gamestop_historical_precovid = gamestop_historical_precovid.rename(columns={'Close': 'Gamestop'})
amc_historical_precovid = amc_historical_precovid.rename(columns={'Close': 'AMC'})
blackberry_historical_precovid = blackberry_historical_precovid.rename(columns={'Close': 'Blackberry'})
btc_historical_precovid = btc_historical_precovid.rename(columns={'Close': 'BTC'})

# Use the concat function to combine the DataFrames by column and perform an inner join. 
combined_stocks_precovid_df = pd.concat([tesla_historical_precovid, gamestop_historical_precovid, amc_historical_precovid,blackberry_historical_precovid,btc_historical_precovid], axis="columns", join="inner")

# Sort datetime index in ascending order (past to present)
combined_stocks_precovid_df.sort_index(inplace=True)


# Pulling data for all stocks to be used postcovid
tesla_historical_postcovid = tesla.history(start="2020-03-02", end="2021-06-01")
gamestop_historical_postcovid = gamestop.history(start="2020-03-02", end="2021-06-01")
amc_historical_postcovid = amc.history(start="2020-03-02", end="2021-06-01")
blackberry_historical_postcovid = blackberry.history(start="2020-03-02", end="2021-06-01")
btc_historical_postcovid = btc.history(start="2020-03-02", end="2021-06-01")

# Cleaning data for all stocks to be used postcovid
tesla_historical_postcovid.drop(tesla_historical_postcovid.columns.difference(['Close']), 1, inplace=True)
gamestop_historical_postcovid.drop(gamestop_historical_postcovid.columns.difference(['Close']), 1, inplace=True) 
amc_historical_postcovid.drop(amc_historical_postcovid.columns.difference(['Close']), 1, inplace=True) 
blackberry_historical_postcovid.drop(blackberry_historical_postcovid.columns.difference(['Close']), 1, inplace=True) 
btc_historical_postcovid.drop(btc_historical_postcovid.columns.difference(['Close']), 1, inplace=True) 

# Cleaning final dataframe for postcovid

tesla_historical_postcovid = tesla_historical_postcovid.rename(columns={'Close': 'Tesla'})
gamestop_historical_postcovid = gamestop_historical_postcovid.rename(columns={'Close': 'Gamestop'})
amc_historical_postcovid = amc_historical_postcovid.rename(columns={'Close': 'AMC'})
blackberry_historical_postcovid = blackberry_historical_postcovid.rename(columns={'Close': 'Blackberry'})
btc_historical_postcovid = btc_historical_postcovid.rename(columns={'Close': 'BTC'})


# Use the concat function to combine the DataFrames by column and perform an inner join. 
combined_stocks_postcovid_df = pd.concat([tesla_historical_postcovid, gamestop_historical_postcovid, amc_historical_postcovid,blackberry_historical_postcovid,btc_historical_postcovid], axis="columns", join="inner")

# Sort datetime index in ascending order (past to present)
combined_stocks_postcovid_df.sort_index(inplace=True)

#Daily returns Precovid

daily_returns_precovid = combined_stocks_precovid_df.pct_change()

#Cumulative returns Precovid

cumulative_returns_precovid = (1 + daily_returns_precovid).cumprod()

#Daily returns Postcovid

daily_returns_postcovid = combined_stocks_postcovid_df.pct_change()

#Cumulative returns Postcovid

cumulative_returns_postcovid = (1 + daily_returns_postcovid).cumprod()

#Risk Analysis

memestocks_volatility = daily_returns_postcovid.std()

#Correlation

correlation_postcovid = daily_returns_postcovid.corr()




C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:19: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:20: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:21: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:22: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
C:\Users\Is\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:23: FutureWarning: In a future version of pandas all arguments of DataFrame.drop

### MO Analysis of Precovid Vs Post Covid Memestocks and Bitcoin

In [12]:
# Set asset volume:
tesla_asset = 10
gme_asset = 375
amc_asset = 190
bb_asset = 300
btc_asset=0.25

# Scenario 1 - Start of Covid
tesla_close_price_1 = combined_stocks_postcovid_df.loc["20200302"]["Tesla"]
gme_close_price_1 = combined_stocks_postcovid_df.loc["20200302"]["Gamestop"]
amc_close_price_1 = combined_stocks_postcovid_df.loc["20200302"]["AMC"]
bb_close_price_1 = combined_stocks_postcovid_df.loc["20200302"]["Blackberry"]
btc_close_price_1 = combined_stocks_postcovid_df.loc["20200302"]["BTC"]

## Compute current value of my assets

tesla_value_1 = (tesla_asset) * (tesla_close_price_1)
gme_value_1 = (gme_asset) * (gme_close_price_1)
amc_value_1 = (amc_asset) * (amc_close_price_1)
bb_value_1 = (bb_asset) * (bb_close_price_1)
btc_value_1 = (btc_asset) * (btc_close_price_1)
values_1 = (btc_value_1, bb_value_1,amc_value_1,gme_value_1,tesla_value_1)
total_value_1 = sum(values_1)

# Scenario 2 - Peak of GME price
tesla_close_price_2 = combined_stocks_postcovid_df.loc["20210129"]["Tesla"]
gme_close_price_2 = combined_stocks_postcovid_df.loc["20210129"]["Gamestop"]
amc_close_price_2 = combined_stocks_postcovid_df.loc["20210129"]["AMC"]
bb_close_price_2 = combined_stocks_postcovid_df.loc["20210129"]["Blackberry"]
btc_close_price_2 = combined_stocks_postcovid_df.loc["20210129"]["BTC"]

# Compute current value of my assets
tesla_value_2 = (tesla_asset) * (tesla_close_price_2)
gme_value_2 = (gme_asset) * (gme_close_price_2)
amc_value_2 = (amc_asset) * (amc_close_price_2)
bb_value_2 = (bb_asset) * (bb_close_price_2)
btc_value_2 = (btc_asset) * (btc_close_price_2)
values_2 = (btc_value_2, bb_value_2,amc_value_2,gme_value_2,tesla_value_2)
total_value_2 = sum(values_2)

# Scenario 3 , the day bitcoin reached ATH on April 13th 2021

tesla_close_price_3 = combined_stocks_postcovid_df.loc["20210413"]["Tesla"]
gme_close_price_3 = combined_stocks_postcovid_df.loc["20210413"]["Gamestop"]
amc_close_price_3 = combined_stocks_postcovid_df.loc["20210413"]["AMC"]
bb_close_price_3 = combined_stocks_postcovid_df.loc["20210413"]["Blackberry"]
btc_close_price_3 = combined_stocks_postcovid_df.loc["20210413"]["BTC"]

tesla_value_3 = (tesla_asset) * (tesla_close_price_3)
gme_value_3 = (gme_asset) * (gme_close_price_3)
amc_value_3 = (amc_asset) * (amc_close_price_3)
bb_value_3 = (bb_asset) * (bb_close_price_3)
btc_value_3 = (btc_asset) * (btc_close_price_3)
values_3 = (btc_value_3, bb_value_3,amc_value_3,gme_value_3,tesla_value_3)
total_value_3 = sum(values_2)

# Concat the investment data into one:
meme_scenarios_df = {'Date': ["2020-03-01", "2021-01-29","2021-04-13"], 
      'Tesla': [tesla_value_1,tesla_value_2,tesla_value_3],
      'GME': [gme_value_1,gme_value_2,gme_value_3], 
      'AMC': [amc_value_1,amc_value_2,amc_value_3],
      'BB': [bb_value_1,bb_value_2,bb_value_3],
      'BTC': [btc_value_1,btc_value_2,btc_value_3]}
meme_investment_df = pd.DataFrame(data=meme_scenarios_df)

scenarios_plot = meme_investment_df.set_index('Date')

### Panel Visualization Functions

In [13]:
def create_plot_line_chart(data, title, xlabel, ylabel, figsize):
    """
    Create a line chart based in the data argument.
    """
    new_plot_line_chart = data.plot(
    title=title, xlabel=xlabel, rot=45, ylabel=ylabel,figsize=figsize)
    return new_plot_line_chart

def create_hvplot_bar_chart(data, title, height, width):
    """
    Create a barplot based in the data argument.
    """
    new_hvplot_bar_chart = data.hvplot.bar(
    title=title,  rot=45, height=height, shared_axes=False)
    #plt.show()  
    return new_hvplot_bar_chart 

def create_hvplot_line_chart(data,  title, height, width):
    """
    Create a line chart based in the data argument.
    """
    new_hvplot_line_chart = data.hvplot(
    title=title, rot=45, height=height, width=width, shared_axes=False)
    #plt.show() 
    return new_hvplot_line_chart

def create_scatter_chart(data, title, x, y, color, height):
    """
    Create a line chart based in the data argument.
    """
    new_scatter_chart = px.scatter(data, title=title, x=x, y=y, color=color, height=height)
    #plt.show() 
    return new_scatter_chart

def create_line_chart(data, title, x, y, height, width):
    """
    Create a line chart based in the data argument.
    """
    new_line_chart = px.line(data, title=title, x=x, y=y, height=height)
    #plt.show() 
    return new_line_chart

def create_hvplot_area(data, title, height, width, stacked):
    """
    Create a area plot based in the data argument.
    """
    new_hvplot_area = data.hvplot.area(
    title=title, rot=45, height=height, width=width, stacked=False, shared_axes=False)
    return new_hvplot_area

## Panel Dashboard

In this section, you will combine all of the plots into a single dashboard view using Panel. Be creative with your dashboard design!

In [31]:
# Create a Title for the Dashboard
 
# Define a welcome text
#welcometab = "Welcome Text here"
welcometab =  """ <h2><b>Cryptocurrency and Financial Analysis in the Covid-Era. </b></h2> <br><br> <h3><b>Welcome to this Dashboard! </b></h3>Please click along the tabs at the top to peruse the various data visualizations. <br> This dashboard aims to present a visual analysis of Cryptocurrency and Financial Analysis in the Covid-Era.<br><br> Enjoy!   
"""

 

#define column 2001 bar chart
ben1_create_pre_c_returns = pn.Column(
    "## Pre-Covid Daily Returns, Combined", 
    create_hvplot_line_chart(pre_daily_returns, title='Pre-Covid Daily Returns: Semiconductors VS Crypto Stocks', height=400, width=800))

ben1_create_post_c_returns = pn.Column(
    "## Post-Covid Daily Returns, Combined", 
    create_hvplot_line_chart(post_daily_returns, title='Post-Covid Daily Returns: Semiconductors VS Crypto Stocks', height=400, width=800))


ben1_create_pre_cumu_returns = pn.Column(
    "## Pre-Covid Daily Returns, Combined",
    create_hvplot_line_chart(pre_cumulative_returns, title='Pre-Covid Cumulative Returns: Semiconductors VS Crypto Stocks', height=400, width=800))

ben1_create_post_cumu_returns = pn.Column(
    "## Post-Covid Daily Returns, Combined",
    create_hvplot_line_chart(post_cumulative_returns, title='Post-Covid Cumulative Returns: Semiconductors VS Crypto Stocks', height=400, width=800))

ben1_create_covid_cumulative_cases = pn.Column(
    "## Mar 2020 to Mar 2021: Cumulative Covid Cases",
    create_scatter_chart(ben_df_cumu_cases, title="Mar 2020 to Mar 2021: Cumulative Covid Cases", x="Date", y="Cumulative_cases", color="Cumulative_cases",  height=400))

ben1_create_btc_semi_cumulative_cases = pn.Column(
    "## BTC Vs. Semiconductor ETF w/ Covid Cases",
            create_scatter_chart(result, x="BTC", y="Semiconductor ETF", color="Cumulative_cases", title="BTC Vs. Semiconductor ETF w/ Covid Cases", height=500))

ben1_create_ltcbtc_semi_cumulative_cases = pn.Column(
    "## BTC Vs. Semiconductor ETF w/ Covid Cases",
    create_scatter_chart(result, x="BTC", y="LTC", color="Cumulative_cases", title="BTC, LTC w/ Covid Cases", height=500)
)

ben3_create_line_compare_results = pn.Column(
    "## My investment during Covid: Crypto VS. Semiconductors (2020-2021)",
    create_hvplot_line_chart(compare_results, title="My investment during Covid: Crypto VS. Semiconductors (2020-2021)", height=400, width=800)
)

ben3_create_bar_compare_results = pn.Column(
    "## 3 timepoint analysis: Crypto VS. Semiconductors (2020-2021)",
    create_hvplot_bar_chart(compare_results,title="My investment during Covid: Crypto VS. Semiconductors (2020-2021)", height=400, width=800)
)

# Sadia define plots
sadia_create_pre_c_returns = pn.Column(create_hvplot_line_chart(daily_returns, title="Daily Returns - PreCovid", height=400, width=800))
sadia_create_post_c_returns = pn.Column(create_hvplot_line_chart(daily_returns_post_covid, title="Daily Returns - Post Covid", height=400, width=800))
sadia_create_pre_c_creturns = pn.Column(create_hvplot_area(cumulative_returns, title="Cumulative Returns - PreCovid", height=400, width=800, stacked=False))
sadia_create_post_c_creturns = pn.Column(create_hvplot_area(cumulative_returns_post_covid, title="Cumulative Returns - Post Covid", height=400, width=800, stacked=False))

sadia_create_corr_pre_c = pn.Column(create_hvplot_line_chart(correlation, title="Correlation - PreCovid", height=300, width=600))
sadia_create_corr_post_c = pn.Column(create_hvplot_line_chart(correlation_post_covid, title="Correlation - Post Covid", height=300, width=600))
sadia_create_all_creturns = pn.Column("Bitcoin has experienced a steady rise to new all-time highs, breaking through 20,000 USD per BTC, as of December 2020, but the climb has not been a steady one. Taking a look at Ethereum (ETH) fell from an early-year high of 1,300 USD to just 91 USD by December 2018, before rallying back to over 450 USD by the end of 2020. Cryptocurrencies such as Bitcoin and Ethereum have proven to be extremely resilient, causing retail and institutional investor interest in digital currencies to rise dramatically in recent months. And indicating that there are still reasons to believe that the cryptocurrency industry has some fight left in it.", create_hvplot_area(cumulative_returns_overall, title="Cumulative Returns - Overall", height=400, width=800, stacked=False))

sadia_create_covid_cases = pn.Column(create_line_chart(df_covid_cumulative_cases, title="Rise in Covid Cases", x=df_covid_cumulative_cases.index, y="Cumulative_cases", height=300, width=700))
sadia_create_post_covid_plot = pn.Column(create_hvplot_line_chart(postcovid_data, title="Cryptocurrency and Gold Prices", height=300, width=700))
sadia_create_results = pn.Column("The pandemic as managed to ascertain that people have shifted towards safe-haven assets. Although gold has given good returns, crypto has given even better returns than gold and that is why, crypto can be considered as the new hot cake in terms of investment. In terms of final verdict, Bitcoin has outperformed gold as a store of value 100 times over. The rest of the world is catching on and starting to price digital currency in real time. Although Bitcoin has increased many times in the last few months, it is expected to continue increasing in US dollar terms in the coming years. Perhaps by 2030, the market capitalization of Bitcoin will exceed that of gold. Both gold and cryptocurrency have advantages and disadvantages. It is entirely up to the investor to decide where they want to invest.", create_hvplot_line_chart(compare_results, title="My investment during Covid: Crypto VS. Gold (2020-2021)", height=500, width=1000))


mo1_create_precovid_daily_returns=pn.Column(create_hvplot_area(daily_returns_precovid,"Daily Returns Precovid",height=400, width=800,stacked=False))

mo1_create_postcovid_daily_returns=pn.Column(create_hvplot_area(daily_returns_postcovid,"Daily Returns Precovid",height=400, width=800,stacked=False))

mo1_create_precovid_cumulative_returns=pn.Column(create_hvplot_area(cumulative_returns_precovid,"Cumulative Returns Precovid",height=400, width=800,stacked=False))

mo1_create_postcovid_cumulative_returns=pn.Column(create_hvplot_area(cumulative_returns_postcovid,"Cumulative Returns Precovid",height=400, width=800,stacked=False))

mo2_correlation_mem_vs_btc_postcovid = pn.Column(create_hvplot_line_chart(correlation_postcovid, title="Correlation: Meme vs Btc - PostCovid", height=400, width=800))

mo3_bar_investment = pn.Column(
    create_hvplot_bar_chart(meme_investment_df, title="Catching the Market:Portfolio Peaks during Covid", height=400, width=800)
)

mo3_scenarios_plot = pn.Column(create_hvplot_line_chart(scenarios_plot, title="Catching the Market:A Hypothetical Gain Scenario Based on Peaks", height=400, width=800)
    )

# Mo tabs

## Define returns


bentab1 = pn.Column(
                   pn.Row(ben1_create_pre_c_returns, ben1_create_post_c_returns), 
                   pn.Row(ben1_create_pre_cumu_returns, ben1_create_post_cumu_returns)
                   )

bentab2 = pn.Column(pn.Row(ben1_create_covid_cumulative_cases,ben1_create_post_cumu_returns ), 
                    pn.Row(ben1_create_ltcbtc_semi_cumulative_cases,ben1_create_btc_semi_cumulative_cases ), )

bentab3 = pn.Column(pn.Row(ben3_create_line_compare_results, ben3_create_bar_compare_results), 
                     )
    


sadiatab1_column = pn.Row(pn.Column(sadia_create_pre_c_returns, sadia_create_post_c_returns), pn.Column(sadia_create_pre_c_creturns, sadia_create_post_c_creturns))
sadiatab2_column = pn.Row(pn.Column(sadia_create_corr_pre_c, sadia_create_corr_post_c), sadia_create_all_creturns)
sadiatab3_column = pn.Row(pn.Column(sadia_create_covid_cases, sadia_create_post_covid_plot), sadia_create_results)

motab1_column = pn.Column(
                   pn.Row(mo1_create_precovid_daily_returns, mo1_create_postcovid_daily_returns), 
                   pn.Row(mo1_create_precovid_cumulative_returns, mo1_create_postcovid_cumulative_returns)
                   )


motab2_column = pn.Row(mo2_correlation_mem_vs_btc_postcovid)

motab3_column = pn.Column(mo3_bar_investment, mo3_scenarios_plot)

conclusiontab1_column = pn.Column()
conclusiontab2_column = pn.Column()



 
#tab for yearly analysis 
#tab1 = pn.Column(create_hvplot_line_column)
 

# Create a tab layout for the dashboard
# Create the main dashboard

my_dashboard = pn.panel(
    
pn.Row(pn.Tabs(
    ("Welcome", welcometab),    
    ("Semiconductor/Crypto", bentab1), 
    ("Covid/Crypto", bentab2), 
    ("3-Point-Analysis", bentab3),
    ("Comparative: Post and Pre Crypto & Meme", motab1_column), 
    ("Meme stocks Correlation Postcovid", motab2_column),
    ("Catching the Market:A hypothetical Gain Scenario", motab3_column),
    ("Daily and Cumulative Returns", sadiatab1_column), 
    ("Correlation and Covid", sadiatab2_column),
    ("Investment in Covid", sadiatab3_column),
    #("conclusiontab1", conclusiontab1_column), 
    #("conclusiontab2", conclusiontab2_column), 
      
               sizing_mode='stretch_width', 
             
                
    
 #end tabs   
), height=900 
      
#end rows
)
 
#end panel
)

## Serve the Panel Dashboard

In [32]:
#please ignore error messages, the dashboard works on local machine. 
#please see gif recording as well, for data visualization / graphs / charts 
my_dashboard.servable(location=True, area='main')

Row(height=900)
    [0] Tabs(sizing_mode='stretch_width')
        [0] Markdown(str, name='Welcome')
        [1] Column
            [0] Row
                [0] Column
                    [0] Markdown(str)
                    [1] HoloViews(NdOverlay)
                [1] Column
                    [0] Markdown(str)
                    [1] HoloViews(NdOverlay)
            [1] Row
                [0] Column
                    [0] Markdown(str)
                    [1] HoloViews(NdOverlay)
                [1] Column
                    [0] Markdown(str)
                    [1] HoloViews(NdOverlay)
        [2] Column
            [0] Row
                [0] Column
                    [0] Markdown(str)
                    [1] Plotly(Figure, visible=False)
                [1] Column
                    [0] Markdown(str)
                    [1] HoloViews(NdOverlay)
            [1] Row
                [0] Column
                    [0] Markdown(str)
                    [1] Plotly(Figure, visible=False)
                [1] Column
                    [0] Markdown(str)
                    [1] Plotly(Figure, visible=False)
        [3] Column
            [0] Row
                [0] Column
                    [0] Markdown(str)
                    [1] HoloViews(NdOverlay)
                [1] Column
                    [0] Markdown(str)
                    [1] HoloViews(Bars)
        [4] Column
            [0] Row
                [0] Column
                    [0] HoloViews(NdOverlay)
                [1] Column
                    [0] HoloViews(NdOverlay)
            [1] Row
                [0] Column
                    [0] HoloViews(NdOverlay)
                [1] Column
                    [0] HoloViews(NdOverlay)
        [5] Row
            [0] Column
                [0] HoloViews(NdOverlay)
        [6] Column
            [0] Column
                [0] HoloViews(Bars)
            [1] Column
                [0] HoloViews(NdOverlay)
        [7] Row
            [0] Column
                [0] Column
                    [0] HoloViews(NdOverlay)
                [1] Column
                    [0] HoloViews(NdOverlay)
            [1] Column
                [0] Column
                    [0] HoloViews(NdOverlay)
                [1] Column
                    [0] HoloViews(NdOverlay)
        [8] Row
            [0] Column
                [0] Column
                    [0] HoloViews(NdOverlay)
                [1] Column
                    [0] HoloViews(NdOverlay)
            [1] Column
                [0] Markdown(str)
                [1] HoloViews(NdOverlay)
        [9] Row
            [0] Column
                [0] Column
                    [0] Plotly(Figure, visible=False)
                [1] Column
                    [0] HoloViews(NdOverlay)
            [1] Column
                [0] Markdown(str)
                [1] HoloViews(NdOverlay)

# Debugging

Note: Some of the Plotly express plots may not render in the notebook through the panel functions.

However, you can test each plot by uncommenting the following code

In [16]:
# create_plot_line_chart(data, title, xlabel, ylabel, stacked, figsize)

In [17]:
# create_hvplot_bar_chart(data, title, xlabel, ylabel, color, height)

In [18]:
# create_hvplot_line_chart(data, title, xlabel, ylabel, color, height)

In [19]:
# create_scatter_chart(data, title, x, y, color, height)

In [20]:
#create_hvplot_line_chart(correlation, title="Correlation - PreCovid", height=300, width=700)

In [21]:
#create_hvplot_line_chart(post_daily_returns, title='Post-Covid Daily Returns: Semiconductors VS Crypto Stocks', height=400, width=800)

In [22]:
#create_hvplot_line_chart(pre_daily_returns, title='Pre-Covid Daily Returns: Semiconductors VS Crypto Stocks', height=400, width=800)

In [23]:
#pre_cumulative_returns.hvplot(height=400, width=800,title='Pre-Covid Cumulative Returns: Daily Returns: Semiconductors VS Crypto Stocks')

In [24]:
#post_cumulative_returns.hvplot(height=400, width=800,title='Post-Covid Cumulative Returns, Combined')

In [25]:
#px.scatter(df_covid_cumulative_cases,   y="Cumulative_cases", color="Cumulative_cases", title="Mar 2020 to Mar 2021: Cumulative Covid Cases")

In [26]:
#px.scatter(result, x="BTC",  y="Semiconductor ETF", color="Cumulative_cases", title="BTC Vs. Semiconductor ETF w/ Covid Cases", height=500)

In [27]:
#post_cumulative_returns.hvplot(figsize=(200,500),title='Post-Covid Cumulative Returns, Combined')

In [28]:
#compare_results.hvplot(title="My investment during Covid: Crypto VS. Semiconductors (2020-2021)")

In [29]:
#compare_results.hvplot.bar(height=500, title="3 timepoint analysis: Crypto VS. Semiconductors (2020-2021)", rot=45)

In [30]:
# bokeh serve
#op
# navigate to cd C:\Users\benja\FinTechBootCamp\Group Work\PROJECT1FILES\fintech-project1-data-analysis\Python Code
# panel serve --show DashboardAnalysis1_Group.ipynb
# shared_axes=False